<img src="https://avatars.githubusercontent.com/u/74911464?s=200&v=4"
     alt="OpenEO Platform logo"
     style="float: left; margin-right: 10px;" />
# Introduction to openEO  using ILWISPy as backend

Notebook prepared by Ben Maathuis and Bas Retsios. ITC-University of Twente, Enschede. The Netherlands.
Note that authentication details for GEE access was obtained from internet resources (source: https://github.com/Open-EO/openeo-earthengine-driver)

### To get started with openEO Platform review a number of online resources first.

Review the article "The openEO API–Harmonising the Use of Earth Observation Cloud Services Using Virtual Data Cube Functionalities"
https://www.researchgate.net/publication/350109855_The_openEO_API-Harmonising_the_Use_of_Earth_Observation_Cloud_Services_Using_Virtual_Data_Cube_Functionalities

#### Review:
A list of all known openEO providers and their services:
https://hub.openeo.org/

####  Review: 
Check the collections and editor functionality at:
https://editor.openeo.cloud/  

#### Review:
Get some more information on the data cube concepts:
https://openeo.org/documentation/1.0/datacubes.html

Check the required site packages, if not installed already, ensure that they are available before you continue. Install required site packages with command 'pip install *package*'

This notebook will create within this notebook folder a sub-directory 'Intro_openEO_ILWISPy' used to store the downloaded data and will be assigned as your ILWISPy working-directory.

#### Connect to openEO Platform and print list of available collections

In [ ]:
#load required required libraries and install sitepackages
from ctypes import *
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGLdispatch.so.0.0.0')
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGLX.so.0.0.0')
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGL.so.1.7.0')

lib1 = cdll.LoadLibrary('/opt/conda/lib/libpython3.11.so.1.0')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Gui.so.5')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Sql.so.5')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Concurrent.so.5')

import os
import ilwis
import matplotlib.pyplot as plt
from matplotlib.colors import ListedColormap
import openeo
from zipfile import ZipFile
from datetime import date, timedelta, datetime
import numpy as np
from pathlib import Path

#### Import ILWISPy and set working folder

In [ ]:
ilwis.version()

In [ ]:
Path('./Intro_openEO_ILWISPy').mkdir(parents=True, exist_ok=True)

In [ ]:
work_dir = os.getcwd() + '/Intro_openEO_ILWISPy'

#set the working directory for ILWISPy
ilwis.setWorkingCatalog(work_dir)
print(work_dir)

#### Check OpenEO version and connect to the Earth Engine OpenEO Demo Version

In [ ]:
openeo.__version__

In [ ]:
connection = openeo.connect("https://earthengine.openeo.org")

In [ ]:
#connection.authenticate_basic("username", "password")

print("Authenticate with Basic authentication")
connection.authenticate_basic("group1", "test123")

#### Get started with the openEO Python Client. 
Before you continue review the information provided at: https://docs.openeo.cloud/getting-started/python/#connect-to-openeo-platform-and-explore

Processes in openEO are operations that can be applied on (EO) data (e.g. calculate the mean of an array, or mask out observations outside a given polygon). The output of one process can be used as the input of another process, and by doing so, multiple processes can be connected that way in a larger "process graph" that implements a certain algorithm.

In [ ]:
connection.list_processes()

#### Obtain information about available collections  - data sources

In [ ]:
print(connection.list_collection_ids())

In [ ]:
print(connection.list_collections()[0])

#### Print 1st collection from the list
Note the index number, it starts from 0

In [ ]:
print(connection.list_collections()[0:3])

#### Get detailed information about a collection

In [ ]:
print(connection.describe_collection("COPERNICUS/Landcover/100m/Proba-V-C3/Global")) #text listing

connection.describe_collection("COPERNICUS/Landcover/100m/Proba-V-C3/Global") #web listing

#### Load the selected collection, here the spatial extent used is over the Cape Verde islands

In [ ]:
# Load data cube from GEE collection.
cube = connection.load_collection(
    "COPERNICUS/Landcover/100m/Proba-V-C3/Global",
    spatial_extent={"west": -25.5, "south": 14.5, "east": -22.5, "north": 17.25},
    temporal_extent=["2015-01-01", "2019-12-31"],
    bands=["discrete_classification"],
)

In [ ]:
cube.download(r'./Intro_openEO_ILWISPy/lc.GTIFF-ZIP')

In [ ]:
z = ZipFile('./Intro_openEO_ILWISPy/lc.GTIFF-ZIP')
for file in z.filelist:
    outfile = file.filename.replace('download.discrete_classification','CapeVerde_LCC')
    foutp = open('./Intro_openEO_ILWISPy/' + outfile,'wb')
    foutp.write(z.read(file.filename))
    foutp.close()

In [ ]:
# comment lines below if you don't want to remove the downloaded zip file 
z.close()
os.remove('./Intro_openEO_ILWISPy/lc.GTIFF-ZIP')

In [ ]:
#load raster in ILWISPy
rcDC = ilwis.RasterCoverage('CapeVerde_LCC.tif')

In [ ]:
# probe its size
print(rcDC.size().xsize)
print(rcDC.size().ysize)
print(rcDC.size().zsize)

In [ ]:
#transform raster from ILWIS to Numpy
rcDC2np = np.fromiter(iter(rcDC), np.ubyte, rcDC.size().linearSize()) 
rcDC2np = rcDC2np.reshape((rcDC.size().zsize, rcDC.size().ysize, rcDC.size().xsize))
print(rcDC2np.shape)

In [ ]:
#dispay numpy array
plt.imshow(rcDC2np[0], interpolation='none', cmap=ListedColormap(['#00BB22','#00FF4C', '#F096FF', '#FA0000', '#B4B4B4', '#0032C8', '#009696', '#648C00', '#000080'])) 
plt.axis('on')
plt.colorbar(shrink=0.8)
plt.title('LCC over Cape Verde')

In [ ]:
#Export as ILWIS raster map
rcDC.store('CapeVerde_LCC.mpr')

#### Extract rainfall over Zambia for a single day

In [ ]:
connection.describe_collection("UCSB-CHG/CHIRPS/DAILY")

In [ ]:
# create time stamp for single CHIRPS Daily Rainfall map retrieval
year = 2018
month = 1
day_start = 1

date_start = date(year, month, day_start)
start_string = date_start.strftime('%Y%m%d')
print(start_string)

one_day = timedelta(days=1)

date_end = date_start + one_day
end_string = date_end.strftime('%Y%m%d')
print(end_string)

In [ ]:
cube = connection.load_collection(
    "UCSB-CHG/CHIRPS/DAILY",
    spatial_extent={"west": 21.74, "south": -19.31, "east": 34.40, "north": -7.70},
    temporal_extent=[date_start, date_end],
    bands=["precipitation"],
)
cube.download(work_dir+'/pcp_chirps_'+start_string+'_single.GTIFF-ZIP')

In [ ]:
z = ZipFile('./Intro_openEO_ILWISPy/pcp_chirps_'+start_string+'_single.GTIFF-ZIP')
for file in z.filelist:
    outfile = file.filename.replace('download.precipitation','pcp_chirps_'+start_string+'_single')
    foutp = open('./Intro_openEO_ILWISPy/' + outfile,'wb')
    foutp.write(z.read(file.filename))
    foutp.close()

#old_name = './Intro_openEO_ILWISPy/' +outfile
#new_name = './Intro_openEO_ILWISPy/pcp_chirps_'+start_string+'_single.tif'
#os.rename(old_name,new_name)

In [ ]:
# comment lines below if you don't want to remove the downloaded zip file 
z.close()
os.remove('./Intro_openEO_ILWISPy/pcp_chirps_'+start_string+'_single.GTIFF-ZIP')

In [ ]:
#load precipitation raster in ILWIS
pcp_in = ilwis.RasterCoverage('pcp_chirps_'+start_string+'_single.tif')
print(pcp_in)

In [ ]:
# probe its size
print(pcp_in.size().xsize)
print(pcp_in.size().ysize)
print(pcp_in.size().zsize)

In [ ]:
#calculate basis image statistics and show histogram
stats_input = pcp_in.statistics(ilwis.PropertySets.pHISTOGRAM)
print(stats_input.histogram())
print()
print('Minimum: ',stats_input[ilwis.PropertySets.pMIN]) 
print('Maximum: ',stats_input[ilwis.PropertySets.pMAX]) 
print('Mean: ',stats_input[ilwis.PropertySets.pMEAN]) 
print('No pixels - also nodata: ',stats_input[ilwis.PropertySets.pCOUNT]) 
print('No pixels - no nodata: ',stats_input[ilwis.PropertySets.pNETTOCOUNT]) 
print('Sum all: ',stats_input[ilwis.PropertySets.pSUM]) 

print()
x=[a for (a,b) in stats_input.histogram()][:-1] 
y=[b for (a,b) in stats_input.histogram()][:-1]

plt.bar(x,y,label='Rainfall values')
plt.xlabel('Data Range')
plt.ylabel('Data Frequency')
plt.title('Raster Histogram')
plt.ylim(0,25000)
plt.legend()

In [ ]:
#transform from ilwis to numpy array to be able to show it using imshow
pcp_in2np = np.fromiter(iter(pcp_in), np.ubyte, pcp_in.size().linearSize()) 
pcp_in2np = pcp_in2np.reshape((pcp_in.size().zsize, pcp_in.size().ysize, pcp_in.size().xsize))
print(pcp_in2np.shape)

In [ ]:
plt.imshow(pcp_in2np[0], interpolation='none', vmin = 0, vmax = 60, cmap = 'turbo') 
plt.axis('on')
plt.colorbar(shrink=0.8).set_label('mm/day')
plt.title('Rainfall on '+start_string+' over Zambia')

#### Multi temporal import - extract CHIRPS rainfall for a full month

Currently GEE in OpenEO does not facilitate multiband tif file creation and download. Now a loop is used to import single time steps to lateron create a multitemporal dataset

In [ ]:
# Load data cube from GEE collection, example CHIRPS - Daily.

def download(date_start, date_end, date_start_fn):
    cube = connection.load_collection(
        "UCSB-CHG/CHIRPS/DAILY",
        spatial_extent={"west": 21.74, "south": -19.31, "east": 34.40, "north": -7.70},
        temporal_extent=[date_start, date_end],
        bands=["precipitation"],
    )
    cube.download(work_dir+'/pcp_chirps_'+date_start_fn+'.GTIFF-ZIP')
    z = ZipFile(work_dir+'/pcp_chirps_'+date_start_fn+'.GTIFF-ZIP')
    for file in z.filelist:
        outfile = file.filename.replace('download.','')
        outfile = outfile[:-4] + '_' + date_start_fn + '.tif'
        foutp = open(work_dir +'/' + outfile,'wb')
        foutp.write(z.read(file.filename))
        foutp.close()

In [ ]:
#for temporal extent: "2018-01-01", "2018-01-31"
#if you want to change specify appropriate year, month, day_start and day_end (of specified month)

year = 2018
month = 1
day_start = 1
day_end = 31

one_day = timedelta(days=1)

for day in range(day_start,day_end + 1):
    date_start = date(year, month, day)
    date_end = date_start + one_day
    date_start_fn = date_start.strftime('%Y%m%d')
    print('Downloading', date_start_fn)
    download(date_start,date_end,date_start_fn)    

In [ ]:
# comment lines below if you don't want to remove the downloaded zip files
for p in Path('./Intro_openEO_ILWISPy/').glob("*.GTIFF-ZIP"):
    #p.close()
    os.remove(p)

##### Data check using the same time stamp as for the single image download

In [ ]:
rcday1 = ilwis.RasterCoverage('precipitation_20180101.tif')

In [ ]:
rcRain2np = np.fromiter(iter(rcday1), np.float64, rcday1.size().linearSize()) 
rcRain2np = rcRain2np.reshape((rcday1.size().zsize, rcday1.size().ysize, rcday1.size().xsize))
print(rcRain2np.shape)

In [ ]:
stats_rain = rcday1.statistics(ilwis.PropertySets.pHISTOGRAM)
print('PCP-Minimum: ',stats_rain[ilwis.PropertySets.pMIN]) 
print('PCP-Maximum: ',stats_rain[ilwis.PropertySets.pMAX]) 

x=[a for (a,b) in stats_rain.histogram()][:-1] 
y=[b for (a,b) in stats_rain.histogram()][:-1]

In [ ]:
fig, (ax1, ax2) = plt.subplots(ncols=2, figsize=(14, 10))
im = ax1.imshow(rcRain2np[0], cmap = 'turbo')
plt.colorbar(im, ax=ax1, orientation="horizontal")
ax1.set_title("PCP Map")
ax2.plot(x,y,label='Raster Map values')
ax2.set_title("PCP Histogram")
ax2.set_xlabel("PCP value")
ax2.set_ylabel("frequency")

In [ ]:
print(rcday1.size())
print(rcday1.envelope())
coordSys = rcday1.coordinateSystem()
coordSys.toWKT()

In [ ]:
pcpgrf = rcday1.geoReference()
print(pcpgrf)

In [ ]:
#create empty ilwis raster 
pcpAll = ilwis.RasterCoverage()
defNumr = ilwis.DataDefinition(ilwis.NumericDomain('code=value'), ilwis.NumericRange(0, 1000, 0))
pcpAll.setDataDef(defNumr)
pcpAll.setSize(ilwis.Size(1000, 918, 31))
pcpAll.setGeoReference(rcday1.geoReference())

In [ ]:
pcpAllNp = []
for day in range(day_start,day_end + 1):
    date_start = date(year, month, day)
    date_start_fn = date_start.strftime('%Y%m%d')
    filename = 'precipitation_' + date_start_fn + '.tif'
    print('Reading:', filename)
    rc = ilwis.RasterCoverage(filename) # open in ILWIS
    rc2Np = np.fromiter(iter(rc), np.float64, rc.size().linearSize()) #extract pixel data for all layers (1-D)
    rc2Np = rc2Np.reshape((rc.size().ysize, rc.size().xsize)) # reshape to 2-D
    pcpAllNp.append(rc2Np) # append all data to array
pcpAllNp = np.array(pcpAllNp) # create 3 D-array
print(np.shape(pcpAllNp))

In [ ]:
pcpAll.array2raster(pcpAllNp)
print(pcpAll.size())

Check imported data, it's size and value for a given pixel

In [ ]:
print(pcpAll.size())
for day in range(31):
    print(pcpAll.pix2value(ilwis.Pixel(100,101,day)))#just to show that data is there

Uncomment the line below if you want to store the map stack in ILWIS format, you can use the ILWIS386 animation option to review the monthly rainfall product

In [ ]:
#pcpAll.store('pcp_201801.mpl')

From a daily time step the total precipitation for the month retrieved is calculated using the 'aggregate - sum' function

In [ ]:
ilwis.operationMetaData('aggregaterasterstatistics')

In [ ]:
rcSum = ilwis.do('aggregaterasterstatistics', pcpAll, 'sum')

Review raster size and some statistics

In [ ]:
print(rcSum.size())
stats_pcpsum = rcSum.statistics(ilwis.PropertySets.pHISTOGRAM)
print()
print('Minimum: ',stats_pcpsum[ilwis.PropertySets.pMIN]) 
print('Maximum: ',stats_pcpsum[ilwis.PropertySets.pMAX])

Uncomment the line below to write your result to disk

In [ ]:
rcSum.store('pcpsum_201801.mpr')

Transform your result to a Numpy array so it can be visualized using Matplotlib

In [ ]:
rcSum2np = np.fromiter(iter(rcSum), np.float64, rcSum.size().linearSize()) 
rcSum2np = rcSum2np.reshape((rcSum.size().zsize, rcSum.size().ysize, rcSum.size().xsize))
print(rcSum2np.shape)

In [ ]:
plt.imshow(rcSum2np[0], interpolation='none', vmin = 0, vmax = 500, cmap = 'turbo') 
plt.axis('on')
plt.colorbar(shrink=0.8)
plt.title('Rainfall over Zambia')

Continue with another selected collection or create your own code further below.

In [ ]:
datacube = connection.load_collection(
  "COPERNICUS/S1_GRD",
  spatial_extent={"west": 16.06, "south": 48.06, "east": 16.65, "north": 48.35},
  temporal_extent=["2017-03-01", "2017-04-01"],
  bands=["VV", "VH"]
)

In [ ]:
datacube.download(work_dir+'/S1.GTIFF-ZIP')

In [ ]:
z = ZipFile('./Intro_openEO_ILWISPy/S1.GTIFF-ZIP')
for file in z.filelist:
    outfile = file.filename.replace('download.','')
    foutp = open('./Intro_openEO_ILWISPy/' + outfile,'wb')
    foutp.write(z.read(file.filename))
    foutp.close()

In [ ]:
VV = ilwis.RasterCoverage('VV.tif')
VH = ilwis.RasterCoverage('VH.tif')

In [ ]:
#calculate the cross polarized image (vv/vh)
VC = ilwis.do('mapcalc','(@1/@2)', VV, VH)

In [ ]:
#create histogram using large number of bins, given the fact that the input image is a float64, with both positive and negative numbers
hist = VC.statistics(ilwis.PropertySets.pHISTOGRAM, 65535)
minPerc1, maxPerc1 = hist.calcStretchRange(1)
VCs = ilwis.do('linearstretch',VC, minPerc1, maxPerc1)
VCs = ilwis.do('setvaluerange', VCs, 0, 255, 1)
VCs.store('VCs.mpr')

In [ ]:
VVs = ilwis.do('linearstretch',VV, 1)
VVs = ilwis.do('setvaluerange', VVs, 0, 255, 1)
VVs.store('VVs.mpr')
VV_2np = np.fromiter(iter(VVs), np.ubyte, VVs.size().linearSize()) 
VV_2np = VV_2np.reshape((VVs.size().ysize, VVs.size().xsize))

VHs = ilwis.do('linearstretch',VH, 1)
VHs = ilwis.do('setvaluerange', VHs, 0, 255, 1)
VHs.store('VHs.mpr')
VH_2np = np.fromiter(iter(VHs), np.ubyte, VHs.size().linearSize()) 
VH_2np = VH_2np.reshape((VHs.size().ysize, VHs.size().xsize))

#VCs = ilwis.do('linearstretch',VC_adjust, 1)
#VCs = ilwis.do('setvaluerange', VCs, 0, 255, 0.001)
#VCs.store('VCs.mpr')
VC_2np = np.fromiter(iter(VCs), np.ubyte, VCs.size().linearSize()) 
VC_2np = VC_2np.reshape((VCs.size().ysize, VCs.size().xsize))

In [ ]:
# create  color composite (in RGB)
cc = np.dstack((VV_2np, VH_2np, VC_2np))

In [ ]:
plt.figure(figsize=(10, 7))
plt.imshow(cc, interpolation ='nearest')
plt.title('S1 polarization composite showing the area in the neighborhood of Vienna')

#### Now connect to dataspace.copernicus.eu

This requires registration at: https://dataspace.copernicus.eu/, select the option "Login" and if you don't have an account, create a new account and sign in.

In [ ]:
connection = openeo.connect("openeo.dataspace.copernicus.eu").authenticate_oidc()

In [ ]:
print(connection.list_collection_ids())

In [ ]:
connection.describe_collection("SENTINEL2_L2A")

#### Retrieve Sentinel 2 data
Select for a given temporal range and area of interest, using a cloud cover threshold the 10 meter spatial resolution channels, b2, b3, b4 and b8 (visible blue, green and red as well as the near infrared spectral channels)

In [ ]:
t = ["2023-04-01", "2023-06-30"]
s2_cube = connection.load_collection("SENTINEL2_L2A",
    spatial_extent={'west': 5.00, 'east': 5.38, 'south': 52.58, 'north': 52.80,"crs": "EPSG:4326",},
    temporal_extent= t,
    bands=['B02', 'B03', 'B04', 'B08'],
    max_cloud_cover=1,
)

#### Temporal aggregation
From the selected images, perform a temporal aggregation, using the 'median' value for each pixel in your time series

In [ ]:
s2_cube_red = s2_cube.median_time()

#### Download the selected dataset

In [ ]:
s2_cube_red.download("./Intro_openEO_ILWISPy/Enkhuizen.tif")

#### Further raster image processing
Load the downloaded image in ILWISPy, select the 4 spectral channels as Blue, Green, Red and IR, calculate statistics and conduct a linear stretch operation 

In [ ]:
raster = ilwis.RasterCoverage ('Enkhuizen.tif')
print(raster.size())

In [ ]:
Blue =  ilwis.do('selection',raster,"rasterbands(0)")
Green = ilwis.do('selection',raster,"rasterbands(1)")
Red = ilwis.do('selection',raster,"rasterbands(2)")
IR = ilwis.do('selection',raster,"rasterbands(3)")
print(IR.size().xsize)
print(IR.size().ysize)
print(IR.size().zsize)

In [ ]:
stat_blue = Blue.statistics(ilwis.PropertySets.pHISTOGRAM, 65535)
minPerc1, maxPerc1 = stat_blue.calcStretchRange(1)
Blues = ilwis.do('linearstretch',Blue, minPerc1, maxPerc1)
Blues = ilwis.do('setvaluerange', Blues, 0, 255, 1)

In [ ]:
stat_green = Green.statistics(ilwis.PropertySets.pHISTOGRAM, 65535)
minPerc1, maxPerc1 = stat_green.calcStretchRange(1)
Greens = ilwis.do('linearstretch',Green, minPerc1, maxPerc1)
Greens = ilwis.do('setvaluerange', Greens, 0, 255, 1)

In [ ]:
stat_red = Red.statistics(ilwis.PropertySets.pHISTOGRAM, 65535)
minPerc1, maxPerc1 = stat_red.calcStretchRange(1)
Reds = ilwis.do('linearstretch',Red, minPerc1, maxPerc1)
Reds = ilwis.do('setvaluerange', Reds, 0, 255, 1)

In [ ]:
stat_ir = IR.statistics(ilwis.PropertySets.pHISTOGRAM, 65535)
minPerc1, maxPerc1 = stat_ir.calcStretchRange(1)
IRs = ilwis.do('linearstretch',IR, minPerc1, maxPerc1)
IRs = ilwis.do('setvaluerange', IRs, 0, 255, 1)

#### Transform to a Numpy array
Transform your stretched layers to a Numpy array, in order to visualize your image as a colour composite, using imshow

In [ ]:
Blues_2np = np.fromiter(iter(Blues), np.ubyte, IRs.size().linearSize()) 
Blues_2np = Blues_2np.reshape((IRs.size().ysize, IRs.size().xsize))

Greens_2np = np.fromiter(iter(Greens), np.ubyte, IRs.size().linearSize()) 
Greens_2np = Greens_2np.reshape((IRs.size().ysize, IRs.size().xsize))

Reds_2np = np.fromiter(iter(Reds), np.ubyte, IRs.size().linearSize()) 
Reds_2np = Reds_2np.reshape((IRs.size().ysize, IRs.size().xsize))

IRs_2np = np.fromiter(iter(IRs), np.ubyte, IRs.size().linearSize()) 
IRs_2np = IRs_2np.reshape((IRs.size().ysize, IRs.size().xsize))

In [ ]:
# create  color composite (in RGB)
fc_S2 = np.dstack((IRs_2np, Reds_2np, Greens_2np))
nc_S2 = np.dstack((Reds_2np, Greens_2np, Blues_2np))
S2ALL = np.array([IRs_2np, Reds_2np, Greens_2np, Blues_2np])

In [ ]:
fig1 = plt.figure(figsize=(15, 10))
plt.subplot(1, 2, 1)
plt.imshow(nc_S2)
plt.title('NC - S2 image retrieved from DataSpace.Copernicus.EU')
plt.subplot(1, 2, 2)
plt.imshow(fc_S2)
plt.title('FC - S2 image retrieved from DataSpace.Copernicus.EU')

#### Export results as a new ILWIS image
Create a new  / empty image and as second step load the data and write the output to disk. Review your results using ILWIS386

In [ ]:
#create empty ilwis raster 
S2_ilw = ilwis.RasterCoverage()
defNumr = ilwis.DataDefinition(ilwis.NumericDomain('code=value'), ilwis.NumericRange(0, 255, 1))
S2_ilw.setDataDef(defNumr)
S2_ilw.setSize(ilwis.Size(2643, 2526, 4))
S2_ilw.setGeoReference(raster.geoReference())

In [ ]:
S2_ilw.array2raster(S2ALL.flatten())

In [ ]:
S2_ilw.store('Enkhuizen.mpl')

#### Four Seasons
Derive the NDVI for the four seasons (summer, autumn, winter and spring) and calulate the Standard Deviation over the different seasons to get an idea of the variability

In [ ]:
#summer
t = ["2022-06-01", "2022-08-31"]
summer = connection.load_collection("SENTINEL2_L2A",
    spatial_extent={'west': 5.00, 'east': 5.38, 'south': 52.58, 'north': 52.80,"crs": "EPSG:4326",},
    temporal_extent= t,
    bands=['B02', 'B03', 'B04', 'B08'],
    max_cloud_cover=1,
)

In [ ]:
summer_red = summer.median_time()

In [ ]:
summer_red.download("./Intro_openEO_ILWISPy/summer.tif")

In [ ]:
#autumn - note cloud cover has been set differently elso no image would qualify!
t = ["2022-09-01", "2022-11-30"]
autumn = connection.load_collection("SENTINEL2_L2A",
    spatial_extent={'west': 5.00, 'east': 5.38, 'south': 52.58, 'north': 52.80,"crs": "EPSG:4326",},
    temporal_extent= t,
    bands=['B02', 'B03', 'B04', 'B08'],
    max_cloud_cover=20,
)

In [ ]:
autumn_red = autumn.median_time()

In [ ]:
autumn_red.download("./Intro_openEO_ILWISPy/autumn.tif")

In [ ]:
#winter
t = ["2022-12-01", "2023-02-28"]
winter = connection.load_collection("SENTINEL2_L2A",
    spatial_extent={'west': 5.00, 'east': 5.38, 'south': 52.58, 'north': 52.80,"crs": "EPSG:4326",},
    temporal_extent= t,
    bands=['B02', 'B03', 'B04', 'B08'],
    max_cloud_cover=1,
)

In [ ]:
winter_red = winter.median_time()

In [ ]:
winter_red.download("./Intro_openEO_ILWISPy/winter.tif")

In [ ]:
#spring - note cloud cover has been set differently elso no image would qualify!
t = ["2023-03-01", "2023-03-31"]
spring = connection.load_collection("SENTINEL2_L2A",
    spatial_extent={'west': 5.00, 'east': 5.38, 'south': 52.58, 'north': 52.80,"crs": "EPSG:4326",},
    temporal_extent= t,
    bands=['B02', 'B03', 'B04', 'B08'],
    max_cloud_cover=20,
)

In [ ]:
spring_red = spring.median_time()

In [ ]:
spring_red.download("./Intro_openEO_ILWISPy/spring.tif")

In [ ]:
summer = ilwis.RasterCoverage ('summer.tif')
autumn = ilwis.RasterCoverage ('autumn.tif')
winter = ilwis.RasterCoverage ('winter.tif')
spring = ilwis.RasterCoverage ('spring.tif')

In [ ]:
summer_Red = ilwis.do('selection',summer,"rasterbands(2)")
summer_IR = ilwis.do('selection',summer,"rasterbands(3)")
summer_ndvi = ilwis.do('mapcalc','(@1 - @2)/(@1 + @2)', summer_IR, summer_Red)
summer_ndvi = ilwis.do('setvaluerange', summer_ndvi, -1, 1, 0.001)

In [ ]:
autumn_Red = ilwis.do('selection',autumn,"rasterbands(2)")
autumn_IR = ilwis.do('selection',autumn,"rasterbands(3)")
autumn_ndvi = ilwis.do('mapcalc','(@1 - @2)/(@1 + @2)', autumn_IR, autumn_Red)
autumn_ndvi = ilwis.do('setvaluerange', autumn_ndvi, -1, 1, 0.001)

In [ ]:
winter_Red = ilwis.do('selection',winter,"rasterbands(2)")
winter_IR = ilwis.do('selection',winter,"rasterbands(3)")
winter_ndvi = ilwis.do('mapcalc','(@1 - @2)/(@1 + @2)', winter_IR, winter_Red)
winter_ndvi = ilwis.do('setvaluerange', winter_ndvi, -1, 1, 0.001)

In [ ]:
spring_Red = ilwis.do('selection',spring,"rasterbands(2)")
spring_IR = ilwis.do('selection',spring,"rasterbands(3)")
spring_ndvi = ilwis.do('mapcalc','(@1 - @2)/(@1 + @2)', spring_IR, spring_Red)
spring_ndvi = ilwis.do('setvaluerange', spring_ndvi, -1, 1, 0.001)

In [ ]:
summer_ndvi_2np = np.fromiter(iter(summer_ndvi), np.float64, summer_ndvi.size().linearSize()) 
summer_ndvi_2np = summer_ndvi_2np.reshape((summer_ndvi.size().ysize, summer_ndvi.size().xsize))

autumn_ndvi_2np = np.fromiter(iter(autumn_ndvi), np.float64, summer_ndvi.size().linearSize()) 
autumn_ndvi_2np = autumn_ndvi_2np.reshape((summer_ndvi.size().ysize, summer_ndvi.size().xsize))

winter_ndvi_2np = np.fromiter(iter(winter_ndvi), np.float64, summer_ndvi.size().linearSize()) 
winter_ndvi_2np = winter_ndvi_2np.reshape((summer_ndvi.size().ysize, summer_ndvi.size().xsize))

spring_ndvi_2np = np.fromiter(iter(spring_ndvi), np.float64, summer_ndvi.size().linearSize()) 
spring_ndvi_2np = spring_ndvi_2np.reshape((summer_ndvi.size().ysize, summer_ndvi.size().xsize))

In [ ]:
print(summer_ndvi.size())

In [ ]:
#create empty ilwis raster 
S2_ndvi_all = ilwis.RasterCoverage()
defNumr = ilwis.DataDefinition(ilwis.NumericDomain('code=value'), ilwis.NumericRange(-1, 1, 0.001))
S2_ndvi_all.setDataDef(defNumr)
S2_ndvi_all.setSize(ilwis.Size(2643, 2526, 4))
S2_ndvi_all.setGeoReference(summer_ndvi.geoReference())

In [ ]:
S2_ndvi = np.array([summer_ndvi_2np, autumn_ndvi_2np, winter_ndvi_2np, spring_ndvi_2np])

In [ ]:
S2_ndvi_all.array2raster(S2_ndvi.flatten())

In [ ]:
S2_ndvi_all.store('S2_ndvi.mpl')

In [ ]:
ilwis.operationMetaData('aggregaterasterstatistics')

In [ ]:
ndvi_std = ilwis.do('aggregaterasterstatistics', S2_ndvi_all, 'standarddev')
ndvi_var = ilwis.do('aggregaterasterstatistics', S2_ndvi_all, 'variance')

In [ ]:
#masking the water using the cloud free composite IR band
ndvi_mask = ilwis.do('mapcalc','iff(@1 < 13,0,1)', IRs)
ndvi_mask = ilwis.do('setvaluerange', ndvi_mask, 0, 1, 1)
ndvi_mask.store('Enkhuizen_mask.mpr')

In [ ]:
ndvi_std_mask = ilwis.do('mapcalc','iff(@1 == 1,@2,0)', ndvi_mask, ndvi_std)
ndvi_var_mask = ilwis.do('mapcalc','iff(@1 == 1,@2,0)', ndvi_mask, ndvi_var)
ndvi_std_mask.store('S2_ndviSTD.mpl')
ndvi_var_mask.store('S2_ndviVAR.mpl')

What can be concluded if looking at the areas with the higher variances and standard deviations